In [ ]:
%matplotlib inline 

###########
#PDF PROCESSING FOR various INPUT 
# DEPENDING ON THE PDF_PROCESSING CLASS
#by Carl Schleussner, Climate Analytics
#carl.schleussner@climateanalytics.org
###########
# IMPORT AND CONFIG 
import numpy as np
import netCDF4 as net
import dimarray as da 
import sys
sys.path.append("./src/")
import itertools
import glob
import datetime
import pickle
import os
import pandas as pd
import matplotlib.pylab as plt 
plt.style.use('ggplot')
plt.rcParams['figure.figsize'] = 8,6

try:
    import pdf_processing as pdf; reload(pdf)
except ImportError:
    raise ImportError(
        "cannot find PDF_Processing code")
    
###########
# Settings
###########

# Set GMT dataset
gmtds='Nasa'

# Set Final year in Extreme Event database with sufficient coverage
# 2013 for GHCND, 2010 for HadEx2
ref_year=2010

# Period length (-1)
per_length=19

#Set annual time axis for input data

# Set range for years for bootstrap sampling 
bs_range=[1951,2010]
timeaxis=np.arange(1951,2011)

# Input datasets
datasets=['GHCND','HadEx2']

# Set plottint colours
colordict={
    datasets[0]:"#0072B2",
    datasets[1]:"#D55E00"}
#["#999999", "#E69F00", "#56B4E9", "#009E73", "#F0E442", "#0072B2", "#D55E00", "#CC79A7"]

# PDF Method (currently defined: hist, python_silverman)
pdf_method='python_silverman'


# Variablelist
varinlist=[
    'TXX',
    'TNN',
    'WSDI',
    'Rx5day',
    'Rx1day'
          ] 

# Get warming level difference
dgmtp=np.load('../GMT_time_series/GMT_0p5_diff_intervals.dat')
ref_period=dgmtp[ref_year][gmtds][::-1]
print '0p5 reference period for ',gmtds,ref_year,': ',ref_period
target_periods=[[ref_year-per_length,ref_year],ref_period]
period_names=['Recent','ref']

varoutdict={
    datasets[0]:{},    
    datasets[1]:{}
}

for varin in varinlist:
    for dataset in varoutdict.keys():
        print varin,dataset
        if dataset =='HadEx2':
            read_in_data=da.read_nc('/Users/carls/Documents/CA_box_sync/Box Sync/Personal_box/CFS_share/0p5_observational_record/data/data_climdex/HadEx2/H2_'+varin+'_1901-2010_RegularGrid_global_3.75x2.5deg_LSmask.nc')['Ann']
        elif dataset =='GHCND':
            read_in_data=da.read_nc('/Users/carls/Documents/CA_box_sync/Box Sync/Personal_box/CFS_share/0p5_observational_record/data/data_climdex/GHCND/GHCND_'+varin+'_1951-2016_RegularGrid_global_2.5x2.5deg_LSmask.nc')['Ann']
            # Set regular integer time axis, dimarray default always adds month and day. Time range 1951-2015
        input_data=da.DimArray(read_in_data[19510101:20100101,:,:], axes=[timeaxis, read_in_data.lat, read_in_data.lon],dims=['year', 'lat', 'lon'] )
        
        # Mask for data availability (individual for each dataset)
        varoutdict[dataset][varin]=pdf.PDF_Processing(varin)
        varoutdict[dataset][varin].mask_for_ref_period_data_coverage(input_data,ref_period,check_ref_period_only=False,target_periods=target_periods)

        ###########
        # Derive time slices
        ###########
        varoutdict[dataset][varin].derive_time_slices(input_data,ref_period,target_periods,period_names)
        varoutdict[dataset][varin].derive_distributions()




0p5 reference period for  Nasa 2010 :  [1960, 1979]
TXX HadEx2
No of non-NAN grid cells in Mask over Ref period:  1095
No of non-NAN grid cells in Mask over Ref period and target period  [1991, 2010]  :  831
No of non-NAN grid cells in Mask over Ref period and target period  [1960, 1979]  :  831
no landmask used
Recent [1991, 2010]
ref [1960, 1979]
TXX GHCND
No of non-NAN grid cells in Mask over Ref period:  1488
No of non-NAN grid cells in Mask over Ref period and target period  [1991, 2010]  :  1296
No of non-NAN grid cells in Mask over Ref period and target period  [1960, 1979]  :  1296
no landmask used
Recent [1991, 2010]
ref [1960, 1979]
TNN HadEx2
No of non-NAN grid cells in Mask over Ref period:  1326
No of non-NAN grid cells in Mask over Ref period and target period  [1991, 2010]  :  1082
No of non-NAN grid cells in Mask over Ref period and target period  [1960, 1979]  :  1082
no landmask used
Recent [1991, 2010]
ref [1960, 1979]
TNN GHCND
No of non-NAN grid cells in Mask over 

In [ ]:
###########
# DERIVE PDF/CDFs
###########
try:
    import pdf_processing as pdf; reload(pdf)
except ImportError:
    raise ImportError(
        "cannot find PDF_Processing code")
    
for dataset in varoutdict.keys():
    for varin in varinlist:
        # Derive histogram pdf for target and ref period     
        if varin=='WSDI':
            varoutdict[dataset][varin].derive_pdf_difference('ref','Recent',absolute_scaling=True)
        else:
            varoutdict[dataset][varin].derive_pdf_difference('ref','Recent',pdf_method=pdf_method)

        # Get bootstrapping confidence intervals
        varoutdict[dataset][varin].bootstrapping(bs_range,10)   
        varoutdict[dataset][varin].derive_bootstrapped_conf_interval(pdf_method=pdf_method)


dimarray: 73975 non-null elements (346505 null)
0 / year (60): 1951 to 2010
1 / lat (73): -90.0 to 90.0
2 / lon (96): 0.0 to 356.25
array(...)
Warning, NaNs in bootstrap kernel estimation. No of NaNs:  -56
Warning, NaNs in bootstrap kernel estimation. No of NaNs:  -67
Warning, NaNs in bootstrap kernel estimation. No of NaNs:  -64
Warning, NaNs in bootstrap kernel estimation. No of NaNs:  -53
Warning, NaNs in bootstrap kernel estimation. No of NaNs:  -56
Warning, NaNs in bootstrap kernel estimation. No of NaNs:  -66
Warning, NaNs in bootstrap kernel estimation. No of NaNs:  -56
Warning, NaNs in bootstrap kernel estimation. No of NaNs:  -65
Warning, NaNs in bootstrap kernel estimation. No of NaNs:  -61
Warning, NaNs in bootstrap kernel estimation. No of NaNs:  -65
Warning, NaNs in bootstrap kernel estimation. No of NaNs:  -56
Warning, NaNs in bootstrap kernel estimation. No of NaNs:  -66
Warning, NaNs in bootstrap kernel estimation. No of NaNs:  -56
Warning, NaNs in bootstrap kernel esti

In [ ]:
###########
# PLOTS
###########
f,pl=plt.subplots(nrows=2,ncols=3,figsize=(12,6))
pplot=pl.flatten()

region='global'
distro='pdf'

unit_dict={
    'TXX':'Deg C',
    'TNN':'Deg C',
    'WSDI':'days',
    'Rx5day':'mm',
    'Rx1day':'mm'
          }

from matplotlib import rc
rc('text', usetex=True)

for varin,k in zip(varinlist,range(len(pplot))):
    
    for dataset in varoutdict.keys():

#         pplot[k].plot(varoutdict[dataset][varin]._distributions[region][distro]['xaxis'],
#                  varoutdict[dataset][varin]._distributions[region][distro]['bs_quantiles'][50],color='grey')

        pl5=varoutdict[dataset][varin]._distributions[region][distro]['bs_quantiles'][5]#/varoutdict[dataset][varin]._distributions[region][distro]['bs_quantiles'][50].max()
        pl95=varoutdict[dataset][varin]._distributions[region][distro]['bs_quantiles'][95]#/varoutdict[dataset][varin]._distributions[region][distro]['bs_quantiles'][50].max()
        pplot[k].fill_between(varoutdict[dataset][varin]._distributions[region][distro]['xaxis'],
                        pl95,pl5,color=colordict[dataset],
                              alpha=0.4),#label='90% ref period')

        pplot[k].plot(varoutdict[dataset][varin]._distributions[region][distro]['xaxis'],
                 varoutdict[dataset][varin]._distributions[region][distro]['Recent_ref'],label=varin,color=colordict[dataset])

        pplot[k].legend(loc='upper right')
        pplot[k].set_xlabel(unit_dict[varin])

plt.subplots_adjust(wspace=0.3, hspace=0.3)

# f.suptitle('Observed 0.5 degree difference for HadEX2')
# pplot[1].text(-100, 0.08,'Observed 0.5 degree difference for '+region+' HadEX2 GMT: '+gmtds, fontsize=16,color='grey')
plt.savefig('plots/Observed_0p5_degree_difference_all_DS_'+pdf_method+'.pdf')


In [ ]:
qu5=varoutdict[dataset][varin]._distributions[region][distro]['bs_quantiles'][5]/varoutdict[dataset][varin]._distributions[region][distro]['bs_quantiles'][5].max()
qu95=varoutdict[dataset][varin]._distributions[region][distro]['bs_quantiles'][95]/varoutdict[dataset][varin]._distributions[region][distro]['bs_quantiles'][95].max()

# pl95=np.max([qu5,qu95],axis=0)
# pl5=np.min([qu5,qu95],axis=0)
plt.figure()
plt.plot(qu95)
plt.plot(qu5)
plt.subplots_adjust?
